In [ ]:
pip install transformers datasets accelerate

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 12.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 12.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 9.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 12.6 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [1]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 14.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 18.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 13.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 19.5 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [5]:
from transformers import AutoTokenizer, AutoModelForCausalLM, Trainer, TrainingArguments, DataCollatorForSeq2Seq
from datasets import load_dataset

# Load GPT-Neo tokenizer and model
tokenizer = AutoTokenizer.from_pretrained("EleutherAI/gpt-neo-125M")
model = AutoModelForCausalLM.from_pretrained("EleutherAI/gpt-neo-125M")

# Set pad token to eos token
tokenizer.pad_token = tokenizer.eos_token

# Load the subset dataset
dataset = load_dataset("json", data_files="financial_accounting_subset.json")

# Inspect the first row to verify the structure of the dataset
first_row = next(iter(dataset["train"]))
print("Keys in the dataset:", first_row.keys())

# Define input and output columns based on your dataset structure
# Adjust these as necessary for your task
input_column = "Description"  # Example input: financial transaction description
output_column = "Category"  # Example output: transaction category

# Check if the specified columns exist in the dataset
if input_column not in first_row or output_column not in first_row:
    raise KeyError(
        f"Columns '{input_column}' or '{output_column}' not found in dataset. "
        f"Available keys: {list(first_row.keys())}"
    )

# Define the tokenization function
def tokenize_function(examples):
    inputs = examples[input_column]
    targets = examples[output_column]
    model_inputs = tokenizer(
        inputs,
        truncation=True,
        padding="max_length",
        max_length=512
    )
    with tokenizer.as_target_tokenizer():
        labels = tokenizer(
            targets,
            truncation=True,
            padding="max_length",
            max_length=512
        )
    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

# Tokenize the dataset
tokenized_dataset = dataset.map(tokenize_function, batched=True)

# Optional: Save the tokenized dataset for inspection
tokenized_dataset.save_to_disk("./tokenized_dataset")

print("Tokenization complete!")


Keys in the dataset: dict_keys(['Date', 'Account', 'Description', 'Debit', 'Credit', 'Category', 'Transaction_Type', 'Customer_Vendor', 'Payment_Method', 'Reference'])


Map:   0%|          | 0/50001 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:4114: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


Saving the dataset (0/1 shards):   0%|          | 0/50001 [00:00<?, ? examples/s]

Tokenization complete!


In [6]:
# Define a custom data collator to handle loss computation
class CustomDataCollator(DataCollatorForSeq2Seq):
    def __call__(self, features):
        # Ensure correct padding and label creation
        batch = super().__call__(features)
        labels = batch['input_ids'].clone()
        labels[labels == tokenizer.pad_token_id] = -100  # Ignore padding tokens in the loss computation
        batch['labels'] = labels
        return batch

# Define the training arguments
training_args = TrainingArguments(
    output_dir="./gpt_fine_tuned_model",
    num_train_epochs=1,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    logging_dir='./logs',
    logging_steps=500,
    do_train=True,
    do_eval=True,
    report_to="none",  # Change to "wandb" if using Weights & Biases
)

# Initialize the Trainer with the custom data collator
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset["train"],  # Use the tokenized training dataset
    eval_dataset=tokenized_dataset["train"],   # Optional: if you have a validation set
    data_collator=CustomDataCollator(tokenizer),  # Use custom data collator
)

# Start training
trainer.train()

# Save the fine-tuned model
trainer.save_model("./gpt_fine_tuned_model")


In [7]:
from transformers import AutoTokenizer

# Save model and tokenizer
model.save_pretrained("path_to_save_model")
tokenizer.save_pretrained("path_to_save_model")


('path_to_save_model/tokenizer_config.json',
 'path_to_save_model/special_tokens_map.json',
 'path_to_save_model/vocab.json',
 'path_to_save_model/merges.txt',
 'path_to_save_model/added_tokens.json',
 'path_to_save_model/tokenizer.json')

In [ ]:
results = trainer.evaluate()
print("Evaluation Results:", results)


In [ ]:
test_inputs = [
    "Describe a transaction for a purchase at a retail store.",  # Example prompt
    "Explain a bank deposit transaction.",  # Another example
]

for input_text in test_inputs:
    inputs = tokenizer(input_text, return_tensors="pt", padding=True, truncation=True)
    outputs = model.generate(**inputs, max_length=50)
    generated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)
    print(f"Input: {input_text}")
    print(f"Generated Output: {generated_text}")

In [ ]:
from huggingface_hub import HfApi

api = HfApi()
api.upload_folder(
    folder_path="path_to_save_model",  # Path where the model is saved
    repo_id="your_username/your_model_name",
    repo_type="model"
)


In [ ]:
pip install fastapi uvicorn

In [ ]:
from fastapi import FastAPI, Request
from transformers import AutoModelForCausalLM, AutoTokenizer

app = FastAPI()

model = AutoModelForCausalLM.from_pretrained("path_to_save_model")
tokenizer = AutoTokenizer.from_pretrained("path_to_save_model")

@app.post("/generate")
async def generate(request: Request):
    data = await request.json()
    input_text = data.get("input")
    inputs = tokenizer(input_text, return_tensors="pt", padding=True, truncation=True)
    outputs = model.generate(**inputs, max_length=50)
    return {"output": tokenizer.decode(outputs[0], skip_special_tokens=True)}

# Run using uvicorn
# uvicorn your_script_name:app --reload

In [ ]:
pip install streamlit

In [ ]:
import streamlit as st
from transformers import AutoModelForCausalLM, AutoTokenizer

model = AutoModelForCausalLM.from_pretrained("path_to_save_model")
tokenizer = AutoTokenizer.from_pretrained("path_to_save_model")

st.title("Accounting GPT")
input_text = st.text_input("Enter a prompt:")
if st.button("Generate"):
    inputs = tokenizer(input_text, return_tensors="pt", padding=True, truncation=True)
    outputs = model.generate(**inputs, max_length=50)
    st.write(tokenizer.decode(outputs[0], skip_special_tokens=True))
